### Explainability

In [ ]:
from google.colab import drive
drive.mount('/content/drive/', force_remount=True)

Mounted at /content/drive/


In [ ]:
!pip install transformers
!pip3 install pickle5
!pip install --upgrade --user pandas==1.3
!pip install shap
!pip install captum
!pip install transformers_interpret
!pip install lime

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import torch
import torch.nn as nn
import shap
import scipy as sp
import pickle5 as pickle
import pandas as pd

from captum.attr import IntegratedGradients
from captum.attr import InterpretableEmbeddingBase, TokenReferenceBase
from captum.attr import visualization
from pathlib import Path
from transformers import AutoModelForSequenceClassification, AutoTokenizer, TextClassificationPipeline
from transformers_interpret import SequenceClassificationExplainer

In [ ]:
def score_and_visualize_bin(text, pipe):
    prediction = pipe([text])
    print(prediction[0])
    explainer = shap.Explainer(pipe)
    shap_values = explainer([text])
    shap_values_ = shap_values[0,:,1]
    shap.plots.text(shap_values_)#, matplotlib=True)

In [ ]:
PROJECT_DIR  = Path('/content/drive/MyDrive/few-shot-mr/')

BASE_MODEL = PROJECT_DIR.joinpath('MR_new/CR-RL-20-NORMAL')
MODELS = [PROJECT_DIR.joinpath(f'MR_new/{model}') for model in ['MR-RL-20-NORMAL', 'MR-RL-S20-0.9_la-0.6_SupCon_only_cls', 'MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all']]

In [ ]:
df = pd.read_csv(PROJECT_DIR.joinpath("df_mr_new.csv"))

In [ ]:
df.head(3)

sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
0  smart , sassy interpretation of the oscar wild...  ...                               0.972880
1  its rawness and vitality give it considerable ...  ...                               0.961268
2  a compendium of solondz 's own worst instincts...  ...                               0.932453

[3 rows x 10 columns]

In [ ]:
df_sample = df[(df['dataset'] == 'test') & ((df['label_pred_normal']==df['label_pred_supcon']) & (df['label']==df['label_pred_softtripleloss'])& (df['label_pred_supcon']!=df['label_pred_softtripleloss']))]
print(df_sample.shape)
df_sample.head(3)

(18, 10)


sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
89   the film 's needlessly opaque intro takes its ...  ...                               0.104212
255  the director 's twitchy sketchbook style and a...  ...                               0.047021
586  the uneven movie does have its charms and its ...  ...                               0.034196

[3 rows x 10 columns]

In [ ]:
idx = 89
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.001427687588147819}, {'label': 'LABEL_1', 'score': 0.9985723495483398}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:59, 179.89s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.2137013077735901}, {'label': 'LABEL_1', 'score': 0.7862986922264099}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.8957880139350891}, {'label': 'LABEL_1', 'score': 0.1042119488120079}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:55, 175.51s/it]              


In [ ]:
idx = 586
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 the uneven movie does have its charms and its ...
label                                                                                    0
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                0
dataset                                                                               test
distance                                                                         19.199507
pred_proba_normal                                                                 0.999683
pred_proba_0.6_supcon_only_cls                                                    0.732051
pred_proba_9_ga0.1_softtripleloss_all                                             0.034196
Name: 586, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:49, 109.80s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.26794975996017456}, {'label': 'LABEL_1', 'score': 0.7320501804351807}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.9658045172691345}, {'label': 'LABEL_1', 'score': 0.03419553115963936}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:51, 111.94s/it]              


In [ ]:
df_sample = df[(df['dataset'] != 'train') & ((df['label_pred_normal']==df['label_pred_supcon']) & (df['label']==df['label_pred_softtripleloss'])& (df['label_pred_supcon']!=df['label_pred_softtripleloss']))]
print(df_sample.shape)
df_sample.head(5)

(666, 10)


sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
31   this boisterous comedy serves up a cruel remin...  ...                               0.667001
89   the film 's needlessly opaque intro takes its ...  ...                               0.104212
126  a rambling ensemble piece with loosely connect...  ...                               0.042421
127  let 's hope -- shall we ? -- that the 'true st...  ...                               0.330386
142  everything 's serious , poetic , earnest and -...  ...                               0.040786

[5 rows x 10 columns]

In [ ]:
idx = 2787
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 laughably , irredeemably awful . \n
label                                                                      0
label_pred_normal                                                          1
label_pred_supcon                                                          1
label_pred_softtripleloss                                                  0
dataset                                                                other
distance                                                           18.272364
pred_proba_normal                                                   0.997715
pred_proba_0.6_supcon_only_cls                                      0.730422
pred_proba_9_ga0.1_softtripleloss_all                               0.043564
Name: 2787, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.0022850623354315758}, {'label': 'LABEL_1', 'score': 0.9977149963378906}]


  0%|          | 0/156 [00:00<?, ?it/s]

Partition explainer: 2it [01:06, 66.15s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.26958224177360535}, {'label': 'LABEL_1', 'score': 0.7304177284240723}]


  0%|          | 0/156 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.9564357399940491}, {'label': 'LABEL_1', 'score': 0.04356423765420914}]


  0%|          | 0/156 [00:00<?, ?it/s]

Partition explainer: 2it [01:00, 60.61s/it]               


In [ ]:
idx = 6356
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 'if you are in the mood for an intelligent wee...
label                                                                                    1
label_pred_normal                                                                        0
label_pred_supcon                                                                        0
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         31.524843
pred_proba_normal                                                                  0.00017
pred_proba_0.6_supcon_only_cls                                                    0.008847
pred_proba_9_ga0.1_softtripleloss_all                                              0.89669
Name: 6356, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:10, 130.74s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.9911527037620544}, {'label': 'LABEL_1', 'score': 0.008847355842590332}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.10331067442893982}, {'label': 'LABEL_1', 'score': 0.8966892957687378}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:08, 128.79s/it]              


In [ ]:
idx = 7335
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a terrible movie that some people will neverth...
label                                                                                    0
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                0
dataset                                                                              other
distance                                                                         20.238016
pred_proba_normal                                                                 0.999801
pred_proba_0.6_supcon_only_cls                                                    0.997581
pred_proba_9_ga0.1_softtripleloss_all                                             0.071873
Name: 7335, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/210 [00:00<?, ?it/s]

Partition explainer: 2it [01:26, 86.23s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.002419030526652932}, {'label': 'LABEL_1', 'score': 0.997580885887146}]


  0%|          | 0/210 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.9281269311904907}, {'label': 'LABEL_1', 'score': 0.07187312096357346}]


  0%|          | 0/210 [00:00<?, ?it/s]

Partition explainer: 2it [01:31, 91.86s/it]               


### Correct prediction

1 - positive

In [ ]:
df_sample = df[(df['dataset'] != 'train') & ((df['label_pred_normal']==df['label_pred_softtripleloss']) & (df['label_pred_supcon']==df['label_pred_softtripleloss']))]
print(df_sample.shape)
df_sample.head(5)

(5654, 10)


sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
0  smart , sassy interpretation of the oscar wild...  ...                               0.972880
1  its rawness and vitality give it considerable ...  ...                               0.961268
2  a compendium of solondz 's own worst instincts...  ...                               0.932453
3  it 's fun , but a psychological mess , with au...  ...                               0.367126
4  a fascinating examination of the joyous , turb...  ...                               0.974149

[5 rows x 10 columns]

In [ ]:
idx = 9470
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 it 's a terrible movie in every regard , and u...
label                                                                                    0
label_pred_normal                                                                        0
label_pred_supcon                                                                        0
label_pred_softtripleloss                                                                0
dataset                                                                              other
distance                                                                          30.94822
pred_proba_normal                                                                 0.000151
pred_proba_0.6_supcon_only_cls                                                    0.122039
pred_proba_9_ga0.1_softtripleloss_all                                             0.038393
Name: 9470, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:27, 87.94s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.8779613375663757}, {'label': 'LABEL_1', 'score': 0.12203869223594666}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.9616073966026306}, {'label': 'LABEL_1', 'score': 0.038392581045627594}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:25, 85.12s/it]               


In [ ]:
idx = 559
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 tells a fascinating , compelling story . \n
label                                                                              1
label_pred_normal                                                                  1
label_pred_supcon                                                                  1
label_pred_softtripleloss                                                          1
dataset                                                                        other
distance                                                                   23.846502
pred_proba_normal                                                           0.999923
pred_proba_0.6_supcon_only_cls                                              0.997599
pred_proba_9_ga0.1_softtripleloss_all                                       0.973401
Name: 559, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 7.727924094069749e-05}, {'label'

  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:40, 40.51s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0024006469175219536}, {'label': 'LABEL_1', 'score': 0.9975993037223816}]


  0%|          | 0/132 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.026599403470754623}, {'label': 'LABEL_1', 'score': 0.9734006524085999}]


  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:38, 38.30s/it]               


In [ ]:
idx = 3986
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 surprisingly insightful \n
label                                                             1
label_pred_normal                                                 1
label_pred_supcon                                                 1
label_pred_softtripleloss                                         1
dataset                                                       other
distance                                                   22.69221
pred_proba_normal                                          0.997459
pred_proba_0.6_supcon_only_cls                             0.995769
pred_proba_9_ga0.1_softtripleloss_all                      0.976792
Name: 3986, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.0025409541558474302}, {'label': 'LABEL_1', 'score': 0.9974591135978699}]


  0%|          | 0/30 [00:00<?, ?it/s]

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls


In [ ]:
idx = 8866
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 as original and insightful as last week 's epi...
label                                                                                    0
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         21.998219
pred_proba_normal                                                                 0.999864
pred_proba_0.6_supcon_only_cls                                                    0.999309
pred_proba_9_ga0.1_softtripleloss_all                                             0.974026
Name: 8866, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:21, 81.76s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0006913395482115448}, {'label': 'LABEL_1', 'score': 0.999308705329895}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.025974156334996223}, {'label': 'LABEL_1', 'score': 0.9740259051322937}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:22, 82.50s/it]               


In [ ]:
idx = 3576
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a venturesome , beautifully realized psycholog...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         21.866774
pred_proba_normal                                                                 0.999909
pred_proba_0.6_supcon_only_cls                                                    0.998702
pred_proba_9_ga0.1_softtripleloss_all                                             0.970394
Name: 3576, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:50, 110.80s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0012975438730791211}, {'label': 'LABEL_1', 'score': 0.9987024068832397}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.029606329277157784}, {'label': 'LABEL_1', 'score': 0.9703936576843262}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:50, 110.79s/it]              


In [ ]:
idx = 8460
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 an exhilarating futuristic thriller-noir , min...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         19.123676
pred_proba_normal                                                                 0.999295
pred_proba_0.6_supcon_only_cls                                                    0.997489
pred_proba_9_ga0.1_softtripleloss_all                                               0.9728
Name: 8460, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:07, 127.78s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.002510758815333247}, {'label': 'LABEL_1', 'score': 0.9974892139434814}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.02720039337873459}, {'label': 'LABEL_1', 'score': 0.9727996587753296}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:12, 132.54s/it]              


In [ ]:

idx = 8482
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a wild , endearing , masterful documentary . \n
label                                                                                  1
label_pred_normal                                                                      1
label_pred_supcon                                                                      1
label_pred_softtripleloss                                                              1
dataset                                                                            other
distance                                                                       23.823807
pred_proba_normal                                                               0.999915
pred_proba_0.6_supcon_only_cls                                                  0.997277
pred_proba_9_ga0.1_softtripleloss_all                                            0.97094
Name: 8482, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 

  0%|          | 0/182 [00:00<?, ?it/s]

Partition explainer: 2it [01:09, 69.68s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.002723268698900938}, {'label': 'LABEL_1', 'score': 0.9972767233848572}]


  0%|          | 0/182 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.029060063883662224}, {'label': 'LABEL_1', 'score': 0.9709398746490479}]


  0%|          | 0/182 [00:00<?, ?it/s]

Partition explainer: 2it [01:09, 69.31s/it]               


In [ ]:
idx = 283
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a solid , psychological action film from hong ...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         23.821306
pred_proba_normal                                                                 0.999922
pred_proba_0.6_supcon_only_cls                                                    0.997918
pred_proba_9_ga0.1_softtripleloss_all                                             0.971732
Name: 283, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'

  0%|          | 0/240 [00:00<?, ?it/s]

Partition explainer: 2it [01:17, 77.36s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0020822721999138594}, {'label': 'LABEL_1', 'score': 0.9979177117347717}]


  0%|          | 0/240 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.028268329799175262}, {'label': 'LABEL_1', 'score': 0.9717317223548889}]


  0%|          | 0/240 [00:00<?, ?it/s]

Partition explainer: 2it [01:17, 77.24s/it]               


In [ ]:
idx = 10598
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 an amazing and incendiary movie that dives str...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         21.540611
pred_proba_normal                                                                 0.999881
pred_proba_0.6_supcon_only_cls                                                    0.999425
pred_proba_9_ga0.1_softtripleloss_all                                             0.971856
Name: 10598, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[

  0%|          | 0/248 [00:00<?, ?it/s]


Partition explainer: 2it [01:59, 119.84s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0005753002478741109}, {'label': 'LABEL_1', 'score': 0.9994246959686279}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.028144260868430138}, {'label': 'LABEL_1', 'score': 0.9718557596206665}]


  0%|          | 0/248 [00:00<?, ?it/s]


Partition explainer: 2it [01:45, 105.25s/it]              


In [ ]:

idx = 6666	
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a thoroughly engaging , surprisingly touching ...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         22.857668
pred_proba_normal                                                                 0.999911
pred_proba_0.6_supcon_only_cls                                                    0.998171
pred_proba_9_ga0.1_softtripleloss_all                                              0.97163
Name: 6666, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/210 [00:00<?, ?it/s]


Partition explainer: 2it [01:30, 90.72s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.001829027314670384}, {'label': 'LABEL_1', 'score': 0.9981709718704224}]


  0%|          | 0/210 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.028369463980197906}, {'label': 'LABEL_1', 'score': 0.9716305136680603}]


  0%|          | 0/210 [00:00<?, ?it/s]


Partition explainer: 2it [01:35, 95.68s/it]               


In [ ]:

idx = 8364 	
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a tender , witty , captivating film about frie...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         25.628386
pred_proba_normal                                                                 0.999903
pred_proba_0.6_supcon_only_cls                                                    0.998815
pred_proba_9_ga0.1_softtripleloss_all                                             0.966264
Name: 8364, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{

  0%|          | 0/248 [00:00<?, ?it/s]


Partition explainer: 2it [01:54, 114.72s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.001185228000395}, {'label': 'LABEL_1', 'score': 0.9988148212432861}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.03373567387461662}, {'label': 'LABEL_1', 'score': 0.9662643074989319}]


  0%|          | 0/248 [00:00<?, ?it/s]


Partition explainer: 2it [01:58, 118.93s/it]              


In [ ]:
idx = 7622
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 delightfully rendered \n
label                                                           1
label_pred_normal                                               1
label_pred_supcon                                               1
label_pred_softtripleloss                                       1
dataset                                                     other
distance                                                25.843138
pred_proba_normal                                        0.981673
pred_proba_0.6_supcon_only_cls                           0.993423
pred_proba_9_ga0.1_softtripleloss_all                    0.969792
Name: 7622, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.01832745037972927}, {'label': 'LABEL_1', 'score': 0.9816725850105286}]


  0%|          | 0/56 [00:00<?, ?it/s]


Partition explainer: 2it [00:14, 14.57s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0065773846581578255}, {'label': 'LABEL_1', 'score': 0.9934226870536804}]


  0%|          | 0/56 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.030207982286810875}, {'label': 'LABEL_1', 'score': 0.9697920083999634}]


  0%|          | 0/56 [00:00<?, ?it/s]


Partition explainer: 2it [00:14, 14.87s/it]               


In [ ]:
idx = 3006
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 daring and beautifully made . \n
label                                                                   1
label_pred_normal                                                       1
label_pred_supcon                                                       1
label_pred_softtripleloss                                               1
dataset                                                             other
distance                                                          21.6434
pred_proba_normal                                                 0.99986
pred_proba_0.6_supcon_only_cls                                   0.999383
pred_proba_9_ga0.1_softtripleloss_all                            0.964395
Name: 3006, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.00013977274647913873}, {'label': 'LABEL_1', 'score': 0.9998601675033569}]


  0%|          | 0/90 [00:00<?, ?it/s]


Partition explainer: 2it [00:30, 30.24s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0006172824068926275}, {'label': 'LABEL_1', 'score': 0.999382734298706}]


  0%|          | 0/90 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.03560507670044899}, {'label': 'LABEL_1', 'score': 0.9643949270248413}]


  0%|          | 0/90 [00:00<?, ?it/s]


Partition explainer: 2it [00:30, 30.92s/it]               


In [ ]:
idx = 4
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 a fascinating examination of the joyous , turb...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         23.690851
pred_proba_normal                                                                 0.999922
pred_proba_0.6_supcon_only_cls                                                    0.998636
pred_proba_9_ga0.1_softtripleloss_all                                             0.974149
Name: 4, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'la

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:05, 125.32s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0013637604424729943}, {'label': 'LABEL_1', 'score': 0.9986361861228943}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.025850621983408928}, {'label': 'LABEL_1', 'score': 0.9741494059562683}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:11, 131.10s/it]              


In [ ]:
idx = 0
print(df_sample.loc[idx, :])
sentence = df_sample.loc[idx, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

sentence                                 smart , sassy interpretation of the oscar wild...
label                                                                                    1
label_pred_normal                                                                        1
label_pred_supcon                                                                        1
label_pred_softtripleloss                                                                1
dataset                                                                              other
distance                                                                         23.165274
pred_proba_normal                                                                 0.999888
pred_proba_0.6_supcon_only_cls                                                    0.997444
pred_proba_9_ga0.1_softtripleloss_all                                              0.97288
Name: 0, dtype: object
MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'la

  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:39, 99.81s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.002556005958467722}, {'label': 'LABEL_1', 'score': 0.9974440336227417}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.027119958773255348}, {'label': 'LABEL_1', 'score': 0.9728800654411316}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:35, 95.13s/it]               


In [ ]:
df_sample = df[(df['dataset'] == 'test') & ((df['label_pred_normal']==df['label_pred_softtripleloss']) & (df['label_pred_supcon']==df['label_pred_softtripleloss']))]
print(df_sample.shape)
df_sample.head(3)

(138, 10)


sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
103  . . . a fascinating curiosity piece -- fascina...  ...                               0.029609
225                         a puzzling experience . \n  ...                               0.963311
241                    all in all , a great party . \n  ...                               0.955209

[3 rows x 10 columns]

In [ ]:
sentence = df_sample.loc[8681, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 8.142741717165336e-05}, {'label': 'LABEL_1', 'score': 0.9999185800552368}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:36, 96.99s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.0009929398074746132}, {'label': 'LABEL_1', 'score': 0.9990070462226868}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.0336480550467968}, {'label': 'LABEL_1', 'score': 0.9663518667221069}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:36, 96.95s/it]               


In [ ]:
sentence = df_sample.loc[4609, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.0003146131057292223}, {'label': 'LABEL_1', 'score': 0.9996854066848755}]


  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:57, 57.31s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.004159578587859869}, {'label': 'LABEL_1', 'score': 0.9958403706550598}]


  0%|          | 0/132 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.03535890951752663}, {'label': 'LABEL_1', 'score': 0.9646411538124084}]


  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:47, 47.54s/it]               


In [ ]:
sentence = df_sample.loc[5589, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.00012433262600097805}, {'label': 'LABEL_1', 'score': 0.9998756647109985}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:50, 110.53s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.00043896917486563325}, {'label': 'LABEL_1', 'score': 0.9995610117912292}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.037799593061208725}, {'label': 'LABEL_1', 'score': 0.9622003436088562}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [01:47, 107.62s/it]              


In [ ]:
sentence = df_sample.loc[241, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)
  cls_explainer = SequenceClassificationExplainer(
      model,
      tokenizer,
      custom_labels=['negative', 'positive']
  )
  attributions = cls_explainer(sentence)
  cls_explainer.visualize()

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 9.319034143118188e-05}, {'label': 'LABEL_1', 'score': 0.9999067783355713}]


  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:51, 51.65s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.4210358262062073}, {'label': 'LABEL_1', 'score': 0.5789641737937927}]


  0%|          | 0/132 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.044790904968976974}, {'label': 'LABEL_1', 'score': 0.9552090764045715}]


  0%|          | 0/132 [00:00<?, ?it/s]

Partition explainer: 2it [00:51, 51.80s/it]               


### Incorrect Predictions

In [ ]:
df_sample = df[(df['dataset'] == 'test') & ((df['label_pred_normal']==df['label_pred_softtripleloss']) & (df['label_pred_supcon']==df['label_pred_softtripleloss'])& (df['label']!=df['label_pred_softtripleloss']))]
print(df_sample.shape)


(16, 10)


sentence  ...  pred_proba_9_ga0.1_softtripleloss_all
5917  . . . planos fijos , tomas largas , un ritmo p...  ...                               0.109170
8052  if the film has a problem , its shortness disa...  ...                               0.034967
4183  it 's not particularly well made , but since i...  ...                               0.036133

[3 rows x 10 columns]

In [ ]:
sentence = df_sample.loc[4183, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.9998903274536133}, {'label': 'LABEL_1', 'score': 0.00010961054067593068}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:16, 136.66s/it]              


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.9396919012069702}, {'label': 'LABEL_1', 'score': 0.06030810624361038}]


  0%|          | 0/248 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.9638667106628418}, {'label': 'LABEL_1', 'score': 0.03613332659006119}]


  0%|          | 0/248 [00:00<?, ?it/s]

Partition explainer: 2it [02:25, 145.11s/it]              


In [ ]:
sentence = df_sample.loc[225, 'sentence']
for model_path_ in MODELS:
  print(f"MODEL: {model_path_}") 
  model = AutoModelForSequenceClassification.from_pretrained(model_path_)
  tokenizer = AutoTokenizer.from_pretrained(model_path_)
  pipe = TextClassificationPipeline(model=model, tokenizer=tokenizer, return_all_scores=True)
  score_and_visualize_bin(sentence, pipe)

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-20-NORMAL
[{'label': 'LABEL_0', 'score': 0.00012731176684610546}, {'label': 'LABEL_1', 'score': 0.9998726844787598}]


  0%|          | 0/56 [00:00<?, ?it/s]

Partition explainer: 2it [00:16, 16.93s/it]               


MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-0.9_la-0.6_SupCon_only_cls
[{'label': 'LABEL_0', 'score': 0.00067081896122545}, {'label': 'LABEL_1', 'score': 0.9993292093276978}]


  0%|          | 0/56 [00:00<?, ?it/s]

...

MODEL: /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all


Some weights of the model checkpoint at /content/drive/MyDrive/wcci2022/MR_new/MR-RL-S20-C25_0.4_m0.7_la-9_ga0.1_SoftTripleLoss_all were not used when initializing RobertaForSequenceClassification: ['ntloss.fc']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'label': 'LABEL_0', 'score': 0.03668905422091484}, {'label': 'LABEL_1', 'score': 0.963310956954956}]


  0%|          | 0/56 [00:00<?, ?it/s]

Partition explainer: 2it [00:17, 17.24s/it]               
